In [22]:
import os
import cv2
import re
import numpy as np
import radiomics
from radiomics import featureextractor
from PIL import Image
import SimpleITK as sitk
import pandas as pd
from collections import Counter
from imutils import paths
import random



In [2]:
DATASET_PATH = "../Datasets/OrigDataset"
SEG_PATH = "../Datasets/new_data"
CSV_FILE_PATH = os.path.join(DATASET_PATH, "GroundTruth.csv")
# define the path to the images and masks dataset
IMAGE_DATASET_PATH = os.path.join(SEG_PATH, "images/")
MASK_DATASET_PATH = os.path.join(SEG_PATH, "masks/")

# Type of tumor
melanoma = []
nevus = []
basal_cell_carcinoma = []
actinic_keratoses_and_intraepithelial_carcinoma = []
benign_keratosis_like_lesions = []
dermatofibroma  = []
vascular_lesion = []

lesion_dict = {
    "MEL": 0, 
    "NV": 1,
    "BCC": 2,
    "AKIEC": 3,
    "BKL": 4,
    "DF": 5,
    "VASC": 6
}


params = 'Params.yaml'


In [3]:
imagePaths = sorted(list(paths.list_images(IMAGE_DATASET_PATH)))
maskPaths = sorted(list(paths.list_images(MASK_DATASET_PATH)))


In [4]:
# Function to convert
def listToString(s):
 
    # initialize an empty string
    str1 = " "
 
    # return string
    return (str1.join(s))


In [5]:
df = pd.read_csv(CSV_FILE_PATH)


In [6]:
extractor = featureextractor.RadiomicsFeatureExtractor(params)
results = []
categories = []

for i in range(len(imagePaths)):
    path_original = imagePaths[i]
    path_label = maskPaths[i]
    original = cv2.imread(path_original)
    original = cv2.cvtColor(original, cv2.COLOR_RGB2GRAY)
    original = Image.fromarray(original, "L")
    original.save("original.png")

    label = cv2.imread(path_label, 0)
    label = Image.fromarray(label, "L")
    label.save("label.png")
    result = extractor.execute("original.png", path_label)
    results.append(result)
    
    # Find part of a string that starts with "ISIC_" and ends with number or numbers
    name = re.findall(r"ISIC_\d+", imagePaths[i])
    
    # Select a row that has given name in column names
    row = df.loc[df['image'] == listToString(name)]

    column_name = None
    
    # Iterate through the columns in the subset to find the matching value
    for col in row.columns:
        if 1.0 in row[col].values:
            column_name = col
            break
    
    # Append it to a list of categories
    categories.append(lesion_dict[column_name])
    
feature_names = list(sorted(filter ( lambda k: k.startswith("original_"), results[0] )))


GLCM is symmetrical, therefore Sum Average = 2 * Joint Average, only 1 needs to be calculated
GLCM is symmetrical, therefore Sum Average = 2 * Joint Average, only 1 needs to be calculated
GLCM is symmetrical, therefore Sum Average = 2 * Joint Average, only 1 needs to be calculated
GLCM is symmetrical, therefore Sum Average = 2 * Joint Average, only 1 needs to be calculated
GLCM is symmetrical, therefore Sum Average = 2 * Joint Average, only 1 needs to be calculated
GLCM is symmetrical, therefore Sum Average = 2 * Joint Average, only 1 needs to be calculated
GLCM is symmetrical, therefore Sum Average = 2 * Joint Average, only 1 needs to be calculated
GLCM is symmetrical, therefore Sum Average = 2 * Joint Average, only 1 needs to be calculated
GLCM is symmetrical, therefore Sum Average = 2 * Joint Average, only 1 needs to be calculated
GLCM is symmetrical, therefore Sum Average = 2 * Joint Average, only 1 needs to be calculated
GLCM is symmetrical, therefore Sum Average = 2 * Joint Avera

In [9]:
samples = np.zeros((len(imagePaths),len(feature_names)))
for case_id in range(0 ,len(imagePaths)):
    a = np.array([])
    for feature_name in feature_names:
        a = np.append(a, results[case_id][feature_name])
    samples[case_id,:] = a
    
# May have NaNs
samples = np.nan_to_num(samples)


In [10]:
len(imagePaths)


60078

In [11]:
len(samples)


60078

In [12]:
len(categories)


60078

In [13]:
Counter(categories)


Counter({1: 40230, 0: 6672, 4: 6588, 2: 3084, 3: 1962, 6: 852, 5: 690})

In [60]:
new_lesion_dict = {
    0: [], 
    1: [],
    2: [],
    3: [],
    4: [],
    5: [],
    6: []
}


length_cat = len(categories)
for i in range(length_cat):
    new_lesion_dict[categories[i]].append(samples[i])
        

In [63]:
X =[]
y = []
for category in new_lesion_dict:
    for i in range(len(new_lesion_dict[category])):
        X.append(new_lesion_dict[category][i])
        y.append(category)
        
temp = list(zip(X, y))
random.shuffle(temp)
res1, res2 = zip(*temp)
# res1 and res2 come out as tuples, and so must be converted to lists.
X, y = list(res1), list(res2)  


In [86]:
df_to_save = pd.DataFrame()


In [68]:
column_names = feature_names.copy()


In [69]:
column_names.append('categories')


In [87]:
for col in column_names:
    df_to_save[col] = []
    

/var/folders/8m/1npctfws7dnc_lbx3mhg9kdc0000gn/T/ipykernel_4213/769385081.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_to_save[col] = []
/var/folders/8m/1npctfws7dnc_lbx3mhg9kdc0000gn/T/ipykernel_4213/769385081.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_to_save[col] = []
/var/folders/8m/1npctfws7dnc_lbx3mhg9kdc0000gn/T/ipykernel_4213/769385081.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider join

In [95]:
df_to_save


Empty DataFrame
Columns: [original_firstorder_10Percentile, original_firstorder_90Percentile, original_firstorder_Energy, original_firstorder_Entropy, original_firstorder_InterquartileRange, original_firstorder_Kurtosis, original_firstorder_Maximum, original_firstorder_Mean, original_firstorder_MeanAbsoluteDeviation, original_firstorder_Median, original_firstorder_Minimum, original_firstorder_Range, original_firstorder_RobustMeanAbsoluteDeviation, original_firstorder_RootMeanSquared, original_firstorder_Skewness, original_firstorder_TotalEnergy, original_firstorder_Uniformity, original_firstorder_Variance, original_glcm_Autocorrelation, original_glcm_ClusterProminence, original_glcm_ClusterShade, original_glcm_ClusterTendency, original_glcm_Contrast, original_glcm_Correlation, original_glcm_DifferenceAverage, original_glcm_DifferenceEntropy, original_glcm_DifferenceVariance, original_glcm_Id, original_glcm_Idm, original_glcm_Idmn, original_glcm_Idn, original_glcm_Imc1, original_glcm_Imc2, original_glcm_InverseVariance, original_glcm_JointAverage, original_glcm_JointEnergy, original_glcm_JointEntropy, original_glcm_MCC, original_glcm_MaximumProbability, original_glcm_SumAverage, original_glcm_SumEntropy, original_glcm_SumSquares, original_gldm_DependenceEntropy, original_gldm_DependenceNonUniformity, original_gldm_DependenceNonUniformityNormalized, original_gldm_DependenceVariance, original_gldm_GrayLevelNonUniformity, original_gldm_GrayLevelVariance, original_gldm_HighGrayLevelEmphasis, original_gldm_LargeDependenceEmphasis, original_gldm_LargeDependenceHighGrayLevelEmphasis, original_gldm_LargeDependenceLowGrayLevelEmphasis, original_gldm_LowGrayLevelEmphasis, original_gldm_SmallDependenceEmphasis, original_gldm_SmallDependenceHighGrayLevelEmphasis, original_gldm_SmallDependenceLowGrayLevelEmphasis, original_glrlm_GrayLevelNonUniformity, original_glrlm_GrayLevelNonUniformityNormalized, original_glrlm_GrayLevelVariance, original_glrlm_HighGrayLevelRunEmphasis, original_glrlm_LongRunEmphasis, original_glrlm_LongRunHighGrayLevelEmphasis, original_glrlm_LongRunLowGrayLevelEmphasis, original_glrlm_LowGrayLevelRunEmphasis, original_glrlm_RunEntropy, original_glrlm_RunLengthNonUniformity, original_glrlm_RunLengthNonUniformityNormalized, original_glrlm_RunPercentage, original_glrlm_RunVariance, original_glrlm_ShortRunEmphasis, original_glrlm_ShortRunHighGrayLevelEmphasis, original_glrlm_ShortRunLowGrayLevelEmphasis, original_glszm_GrayLevelNonUniformity, original_glszm_GrayLevelNonUniformityNormalized, original_glszm_GrayLevelVariance, original_glszm_HighGrayLevelZoneEmphasis, original_glszm_LargeAreaEmphasis, original_glszm_LargeAreaHighGrayLevelEmphasis, original_glszm_LargeAreaLowGrayLevelEmphasis, original_glszm_LowGrayLevelZoneEmphasis, original_glszm_SizeZoneNonUniformity, original_glszm_SizeZoneNonUniformityNormalized, original_glszm_SmallAreaEmphasis, original_glszm_SmallAreaHighGrayLevelEmphasis, original_glszm_SmallAreaLowGrayLevelEmphasis, original_glszm_ZoneEntropy, original_glszm_ZonePercentage, original_glszm_ZoneVariance, original_ngtdm_Busyness, original_ngtdm_Coarseness, original_ngtdm_Complexity, original_ngtdm_Contrast, original_ngtdm_Strength, original_shape2D_Elongation, original_shape2D_MajorAxisLength, original_shape2D_MaximumDiameter, original_shape2D_MeshSurface, original_shape2D_MinorAxisLength, original_shape2D_Perimeter, original_shape2D_PerimeterSurfaceRatio, ...]
Index: []

[0 rows x 103 columns]

In [90]:
list_of_arrays = X.copy()
single_list = y.copy()


In [76]:
len(list_of_arrays[0])


102

In [99]:
for i in range(len(list_of_arrays)):
    list_of_arrays[i] = np.append(list_of_arrays[i], single_list[i])


In [78]:
len(list_of_arrays[0])


103

In [105]:
for array in list_of_arrays:
    #list_of_arrays[i] = pd.concat([list_of_arrays[i], pd.DataFrame([array])], ignore_index=True)
    #list_of_arrays[i] = pd.concat([list_of_arrays[i], pd.Series(single_list[i])])
    
    
    df_to_save = pd.concat([df_to_save, pd.DataFrame([array], columns=df_to_save.columns)], ignore_index=True)
    #df.append(pd.DataFrame([array], columns=df.columns), ignore_index=True)
    
    #df = df.append(pd.DataFrame([array], columns=df.columns), ignore_index=True)
    #df_to_save = df_to_save.append(pd.DataFrame([array], columns=df_to_save.columns), ignore_index=True)
    

In [106]:
df_to_save


original_firstorder_10Percentile  original_firstorder_90Percentile  \
0                                  77.0                             162.0   
1                                  64.0                              96.0   
2                                  73.0                             137.0   
3                                 120.0                             191.0   
4                                  76.0                             145.0   
...                                 ...                               ...   
60073                             128.0                             175.0   
60074                              61.0                             144.0   
60075                             104.0                             171.0   
60076                              18.0                             151.0   
60077                              60.0                             157.0   

       original_firstorder_Energy  original_firstorder_Entropy  \
0                    1.518163e+08                     2.290459   
1                    4.267857e+08                     1.232669   
2                    4.726186e+08                     1.934125   
3                    2.589335e+09                     2.010853   
4                    1.410037e+09                     2.085313   
...                           ...                          ...   
60073                3.244814e+09                     1.792354   
60074                4.935057e+08                     2.208266   
60075                7.804357e+08                     2.041734   
60076                3.880729e+08                     2.763355   
60077                1.750154e+09                     2.490992   

       original_firstorder_InterquartileRange  original_firstorder_Kurtosis  \
0                                        48.0                      2.351248   
1                                        17.0                      3.429680   
2                                        37.0                      2.073204   
3                                        43.0                      2.473451   
4                                        35.0                      2.470766   
...                                       ...                           ...   
60073                                    18.0                      7.000809   
60074                                    58.0                      1.709141   
60075                                    37.0                      2.670836   
60076                                    93.0                      1.708051   
60077                                    64.0                      1.939287   

       original_firstorder_Maximum  original_firstorder_Mean  \
0                            215.0                127.408673   
1                            154.0                 80.481700   
2                            156.0                105.831695   
3                            213.0                159.546304   
4                            171.0                112.160795   
...                            ...                       ...   
60073                        207.0                151.505775   
60074                        161.0                104.141212   
60075                        190.0                140.606658   
60076                        206.0                 76.926250   
60077                        200.0                103.942467   

       original_firstorder_MeanAbsoluteDeviation  original_firstorder_Median  \
0                                      26.461359                       135.0   
1                                      10.097202                        81.0   
2                                      19.355369                       106.0   
3                                      22.837109                       165.0   
4                                      20.342325                       114.0   
...                                          ...                         ...   
60073      

In [107]:
df_to_save.to_csv('../Datasets/AllForSelection.csv')
